In [1]:
import pandas as pd
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', 100)
import os
from tqdm import trange, tqdm
import numpy as np

In [2]:
from PIL import Image
import requests
from transformers import AutoProcessor, CLIPVisionModel

In [3]:
import ssl
from irods.session import iRODSSession

In [4]:
from tools import batch

In [5]:
scratch_dir = "/scratch/leuven/355/vsc35521/"
mango_data_folder = "/ghum/home/ghum_pilot034/TEAM_3/"

In [6]:
try:
    env_file = os.environ['IRODS_ENVIRONMENT_FILE']
except KeyError:
    env_file = os.path.expanduser('~/.irods/irods_environment.json')

ssl_context = ssl.create_default_context(
        purpose=ssl.Purpose.SERVER_AUTH,
        cafile=None, capath=None, cadata=None
        )
ssl_settings = {'ssl_context': ssl_context}

In [7]:
session = iRODSSession(irods_env_file=env_file, **ssl_settings)
collection = session.collections.get("/ghum/home/ghum_pilot034/DATASET_3")

## Paths

In [8]:
df = pd.read_csv('dataset_3.csv')

In [9]:
df['mango_path'] = "/ghum/home/ghum_pilot034/DATASET_3/" + df['IE PID'] + "/" + df['REP PID'] + "/" + df['FL PID'] + "_" + df['NAME']

In [10]:
df['mango_output_path'] = "/ghum/home/ghum_pilot034/TEAM_3/vectors/" + df['IE PID'] + "_" + df['REP PID'] + "_" + df['FL PID'] + "_" + df['NAME']

In [11]:
df['server_path'] = scratch_dir + "DATASET_3/" + df['IE PID'] + "/" + df['REP PID'] + "/" + df['FL PID'] + "_" + df['NAME']

In [12]:
df['server_path_v'] = scratch_dir + "DATASET_3/" + df['IE PID'] + "/" + df['REP PID'] + "/" + df['FL PID'] + "_" + df['NAME'] + '.npy'

In [28]:
def get_matrix(paths):
    vectors = []
    for v in paths:
        if os.path.exists(v):
            vectors.append(np.load(v))
    return np.vstack(vectors)

In [29]:
import altair as alt
alt.data_transformers.disable_max_rows()
from sklearn.manifold import TSNE

In [30]:
def apply_tsne(matrix):
    reduced_data = TSNE().fit_transform(matrix)
    return pd.DataFrame(reduced_data, columns=['a','b'])

In [22]:
alt.Chart(viz_df).mark_point().encode(x='a', y='b')

alt.Chart(...)

In [32]:
matrix_recto = get_matrix(df[df['LABEL'].str.endswith('_R')]['server_path_v'].values)

In [33]:
viz_df_recto = apply_tsne(matrix_recto)

In [34]:
alt.Chart(viz_df_recto).mark_point().encode(x='a', y='b')

alt.Chart(...)

In [35]:
matrix_verso = get_matrix(df[df['LABEL'].str.endswith('_V')]['server_path_v'].values)

In [36]:
viz_df_verso = apply_tsne(matrix_verso)

In [37]:
alt.Chart(viz_df_verso).mark_point().encode(x='a', y='b')

alt.Chart(...)

In [39]:
viz_df_verso.shape

(22864, 2)

In [41]:
collection = session.collections.get("/ghum/home/ghum_pilot034/TEAM_3/vectors")

In [49]:
sum(1 for _ in collection.data_objects)

45731

In [48]:
help(collection)

Help on iRODSCollection in module irods.collection object:

class iRODSCollection(builtins.object)
 |  iRODSCollection(manager, result=None)
 |  
 |  Methods defined here:
 |  
 |  __init__(self, manager, result=None)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  __repr__(self)
 |      Return repr(self).
 |  
 |  move(self, path)
 |  
 |  remove(self, recurse=True, force=False, **options)
 |  
 |  unregister(self, **options)
 |  
 |  walk(self, topdown=True)
 |      Collection tree generator.
 |      
 |      For each subcollection in the directory tree, starting at the
 |      collection, yield a 3-tuple
 |  
 |  ----------------------------------------------------------------------
 |  Static methods defined here:
 |  
 |  normalize_path(*paths, **kw_)
 |      Normalize a path or list of paths.
 |      
 |      We use the iRODSPath class to eliminate extra slashes in,
 |      and (if more than one parameter is given) concatenate, paths.
 |      If th